In [106]:
import argparse
import numpy as np
from time import time
import os

In [107]:
np.random.seed(555)

# preprocess.py

**read_item_index_to_entity_id_file()** in preprocess.py <br>
changes the indeces of the item and entity ids

In [3]:
entity_id2index = dict() 
relation_id2index = dict()
item_index_old2new = dict()

In [4]:
file = 'data/' + 'music' + '/item_index2entity_id.txt' #'../data/' + DATASET + '/item_index2entity_id.txt' Constructs the path of the item index to entity ID mapping file
print('reading item index to entity id file: ' + file + ' ...')
i = 0 #This variable is likely to be used for indexing
for line in open(file, encoding='utf-8').readlines(): # reads the file's content line by line
    item_index = line.strip().split('\t')[0] # removes leading and trailing whitespace characters, splits the line into a list of strings and selects the first element which is assumed to be the item index
    satori_id = line.strip().split('\t')[1] # extracts the second element from the list, which is assumed to be the Satori ID
    item_index_old2new[item_index] = i #This line updates a dictionary named item_index_old2new. It uses the item_index as the key and assigns the value i to it. This is likely used to map old item indexes to new ones.
    entity_id2index[satori_id] = i #This line updates a dictionary named entity_id2index. It uses the satori_id as the key and assigns the value i to it. This is likely used to map entity IDs to their corresponding indices.
    i += 1

reading item index to entity id file: data/music/item_index2entity_id.txt ...


In [14]:
# item_index_old2new

In [15]:
# entity_id2index

In [5]:
print(len(item_index_old2new))
print(len(entity_id2index))
# print()
# print()
# print()

3846
3846


In [7]:
import pandas as pd

file_path = 'data/music/item_index2entity_id.txt'

# Reading CSV and creating a DataFrame
df = pd.read_csv(file_path, sep='\t', header=None, names=['item_index', 'satori_id'])

# Display the DataFrame
print(df)

      item_index  satori_id
0              2          0
1              3          1
2              4          2
3              6          3
4              9          4
...          ...        ...
3841       18722       3841
3842       18738       3842
3843       18739       3843
3844       18740       3844
3845       18741       3845

[3846 rows x 2 columns]


In [13]:
# Count the values in each column
value_counts_item_index = df['item_index'].count()
value_counts_satori_id = df['satori_id'].count()

# Count the distinct values in each column
unique_values_item_index = df['item_index'].nunique()
unique_values_satori_id = df['satori_id'].nunique()

# Display the results
print("Value counts for 'item_index':", value_counts_item_index)
print("Value counts for 'satori_id':", value_counts_satori_id)
print("Distinct values count for 'item_index':", unique_values_item_index)
print("Distinct values count for 'satori_id':", unique_values_satori_id)

Value counts for 'item_index': 3846
Value counts for 'satori_id': 3846
Distinct values count for 'item_index': 3846
Distinct values count for 'satori_id': 3846


**convert_rating()** <br>
for all the artists=items that exist in the item_index2entity_id.txt file and in the user_artists.dat file, it creates a new dataset with users, items=artists and target as columns <br>
for each user, there are rows with all the items that were positively rated and for which the target is 1 and an equal number of negative ratings where target is 0 that were randomly selected from the pool of items that were not positive or negative rated

In [14]:
file_path2 = 'data/music/user_artists.dat'

# Reading CSV and creating a DataFrame
df2 = pd.read_csv(file_path2, sep='\t', header=0)

# Display the DataFrame
print(df2)

       userID  artistID  weight
0           2        51   13883
1           2        52   11690
2           2        53   11351
3           2        54   10300
4           2        55    8983
...       ...       ...     ...
92829    2100     18726     337
92830    2100     18727     297
92831    2100     18728     281
92832    2100     18729     280
92833    2100     18730     263

[92834 rows x 3 columns]


In [15]:
# Count the values in each column
value_counts_userID = df2['userID'].count()
value_counts_artistID = df2['artistID'].count()

# Count the distinct values in each column
unique_values_userID = df2['userID'].nunique()
unique_values_artistID = df2['artistID'].nunique()

# Display the results
print("Value counts for 'userID':", value_counts_userID)
print("Value counts for 'artistID':", value_counts_artistID)
print("Distinct values count for 'userID':", unique_values_userID)
print("Distinct values count for 'artistID':", unique_values_artistID)

# Concatenate the two columns and get the total count of unique pairs
total_unique_pairs_count = df2[['userID', 'artistID']].apply(tuple, axis=1).nunique()
# Display the result
print("Total unique pairs count:", total_unique_pairs_count)

# Count rows where 'your_column' has negative values
negative_values_count = df2[df2['weight'] < 0].shape[0]
# Display the result
print("Number of rows with negative values in 'your_column':", negative_values_count)

Value counts for 'userID': 92834
Value counts for 'artistID': 92834
Distinct values count for 'userID': 1892
Distinct values count for 'artistID': 17632


In [48]:
file = 'data/' + 'music' + '/' + 'user_artists.dat' #'../data/' + DATASET + '/' + RATING_FILE_NAME[DATASET] Constructs a file path by combining the string 'data/' with the value of the variable DATASET and the filename specified in the RATING_FILE_NAME dictionary for the given dataset.

print('reading rating file ...')
item_set = set(item_index_old2new.values()) # creates a set called item_set that contains unique values from the item_index_old2new dictionary. It collects all unique item indices.
user_pos_ratings = dict() #These two lines create two dictionaries, user_pos_ratings and user_neg_ratings, to store positive and negative user ratings. These dictionaries will map user IDs to sets of items.
user_neg_ratings = dict()

for line in open(file, encoding='utf-8').readlines()[1:]: #It then iterates through the lines in the file, skipping the first line which is the header)
    array = line.strip().split('\t') #reads a line from the file, removes leading and trailing whitespace characters, and splits it into a list of strings using the delimiter specified in the SEP dictionary for the given dataset.
#     print(array)
    # remove prefix and suffix quotation marks for BX dataset
#     if DATASET == 'book':
#         array = list(map(lambda x: x[1:-1], array)) # the map() function executes a specified function for each item in an iterable

    item_index_old = array[1] #extracts the item index from the array.
#     print(item_index_old)
    if item_index_old not in item_index_old2new:  # the item is not in the final item set
        continue #checks if the item index is not in the item_index_old2new dictionary, and if it's not, it skips to the next iteration of the loop. This is likely used to filter out items that are not in the final item set
    item_index = item_index_old2new[item_index_old] #maps the old item index to a new item index using the item_index_old2new dictionary.

    user_index_old = int(array[0]) # extracts the user index (converting it to an integer) from the array.
#     print(user_index_old)

    rating = float(array[2]) #  extracts the rating (as a floating-point number) from the array.
#     print(rating)
    if rating >= 0: # checks if the rating is greater than or equal to a threshold value specified in the THRESHOLD dictionary for the given dataset.
        if user_index_old not in user_pos_ratings: # it adds the user_index_old to the user_pos_ratings dictionary, creating a set for the user if it doesn't exist, and adds the item_index to the set.
            user_pos_ratings[user_index_old] = set()
        user_pos_ratings[user_index_old].add(item_index)
#         print(user_pos_ratings)
    else:
        if user_index_old not in user_neg_ratings:
            user_neg_ratings[user_index_old] = set()
        user_neg_ratings[user_index_old].add(item_index)
#         print(user_neg_ratings)

print('converting rating file ...')
writer = open('data/' + DATASET + '/ratings_final.txt', 'w', encoding='utf-8') #../ opens a new file for writing, named 'ratings_final.txt'
user_cnt = 0
user_index_old2new = dict()
# in lines 61-65 creates new indices fot the userIDs in the positive ratings dictionary
for user_index_old, pos_item_set in user_pos_ratings.items(): # iterates through the users in the user_pos_ratings dictionary and their associated positive item sets.
    if user_index_old not in user_index_old2new: # checks if the old user index is not already in the user_index_old2new dictionary.
        user_index_old2new[user_index_old] = user_cnt # If the user index is not in the dictionary, it adds the user index to the user_index_old2new dictionary and assigns a new index (user_cnt) to it.
        user_cnt += 1 #  increments user_cnt to ensure that the new user indices are unique.
    user_index = user_index_old2new[user_index_old] #obtains the new user index from the user_index_old2new dictionary.

    for item in pos_item_set: # iterates through the positive item set associated with the user.
        writer.write('%d\t%d\t1\n' % (user_index, item)) #For each user-item pair, it writes a line to the 'ratings_final.txt' file in the format "user_index\titem\t1". This is likely to represent a positive rating (1).
    unwatched_set = item_set - pos_item_set # calculates a set of unwatched items by taking the difference between the item_set (all items) and the pos_item_set (items the user has positively rated).
    if user_index_old in user_neg_ratings: #checks if the user has negative ratings in the user_neg_ratings dictionary.
        unwatched_set -= user_neg_ratings[user_index_old] #If there are negative ratings, it removes items in the user_neg_ratings set from the unwatched_set.
    for item in np.random.choice(list(unwatched_set), size=len(pos_item_set), replace=False): # it randomly selects items from the unwatched_set using NumPy's random.choice function. The number of items selected is equal to the length of the pos_item_set, and items are not replaced after selection (replace=False).
        writer.write('%d\t%d\t0\n' % (user_index, item)) #For each user-item pair, it writes a line to the 'ratings_final.txt' file in the format "user_index\titem\t0". This is likely to represent a negative rating (0).
writer.close() #closes the 'ratings_final.txt' file.
print('number of users: %d' % user_cnt)
print('number of items: %d' % len(item_set)) #number of unique items

reading rating file ...
['2', '51', '13883']
['2', '52', '11690']
{2: {20}}
['2', '53', '11351']
['2', '54', '10300']
['2', '55', '8983']
['2', '56', '6152']
['2', '57', '5955']
{2: {20, 21}}
['2', '58', '4616']
{2: {20, 21, 22}}
['2', '59', '4337']
['2', '60', '4147']
['2', '61', '3923']
['2', '62', '3782']
{2: {20, 21, 22, 23}}
['2', '63', '3735']
['2', '64', '3644']
{2: {20, 21, 22, 23, 24}}
['2', '65', '3579']
['2', '66', '3312']
['2', '67', '3301']
['2', '68', '2927']
['2', '69', '2720']
['2', '70', '2686']
['2', '71', '2654']
['2', '72', '2619']
['2', '73', '2584']
['2', '74', '2547']
['2', '75', '2397']
['2', '76', '2382']
['2', '77', '2120']
['2', '78', '2119']
['2', '79', '1990']
['2', '80', '1972']
['2', '81', '1948']
['2', '82', '1868']
{2: {20, 21, 22, 23, 24, 25}}
['2', '83', '1792']
['2', '84', '1740']
['2', '85', '1638']
{2: {20, 21, 22, 23, 24, 25, 26}}
['2', '86', '1594']
['2', '87', '1559']
['2', '88', '1553']
['2', '89', '1519']
['2', '90', '1471']
{2: {20, 21, 22, 2

['23', '872', '153']
{2: {32, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31}, 3: {33}, 4: {34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 24}, 5: {44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57}, 6: {64, 65, 66, 67, 68, 69, 70, 71, 58, 59, 60, 61, 62, 63}, 7: {72, 73, 74, 75, 76, 77, 78, 79, 80, 81}, 8: {66, 72, 75, 82, 83, 84, 85, 86, 87, 88, 89, 90, 91, 92}, 9: {96, 97, 98, 99, 100, 101, 102, 103, 93, 94, 95}, 10: {104, 105, 106, 107, 44, 108, 109, 110, 111, 112, 113, 51, 114, 55}, 11: {79, 115, 116, 117, 87}, 12: {96, 100, 43, 118, 119, 120, 121, 122, 123, 124, 125, 126}, 13: {128, 129, 130, 131, 132, 133, 134, 135, 136, 137, 74, 79, 80, 55, 87, 127}, 14: {138, 139, 140, 141, 142, 143, 144, 145, 146, 147, 148, 149, 150, 151, 152, 153}, 15: {160, 161, 162, 163, 164, 165, 166, 53, 154, 155, 156, 157, 158, 159}, 16: {98, 131, 167, 168, 169, 170, 171, 172, 173, 174, 175, 176, 177, 178, 179, 180, 181, 182, 183}, 17: {133, 137, 78, 79, 184, 185, 186, 187}, 18: {192, 193, 194, 36, 52, 18

['41', '1362', '385']
['41', '1363', '379']
['41', '1364', '349']
['41', '1365', '341']
['41', '1366', '336']
['41', '1367', '305']
{2: {32, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31}, 3: {33}, 4: {34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 24}, 5: {44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57}, 6: {64, 65, 66, 67, 68, 69, 70, 71, 58, 59, 60, 61, 62, 63}, 7: {72, 73, 74, 75, 76, 77, 78, 79, 80, 81}, 8: {66, 72, 75, 82, 83, 84, 85, 86, 87, 88, 89, 90, 91, 92}, 9: {96, 97, 98, 99, 100, 101, 102, 103, 93, 94, 95}, 10: {104, 105, 106, 107, 44, 108, 109, 110, 111, 112, 113, 51, 114, 55}, 11: {79, 115, 116, 117, 87}, 12: {96, 100, 43, 118, 119, 120, 121, 122, 123, 124, 125, 126}, 13: {128, 129, 130, 131, 132, 133, 134, 135, 136, 137, 74, 79, 80, 55, 87, 127}, 14: {138, 139, 140, 141, 142, 143, 144, 145, 146, 147, 148, 149, 150, 151, 152, 153}, 15: {160, 161, 162, 163, 164, 165, 166, 53, 154, 155, 156, 157, 158, 159}, 16: {98, 131, 167, 168, 169, 170, 171, 172, 173, 174, 175, 176,

['65', '808', '136']
{2: {32, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31}, 3: {33}, 4: {34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 24}, 5: {44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57}, 6: {64, 65, 66, 67, 68, 69, 70, 71, 58, 59, 60, 61, 62, 63}, 7: {72, 73, 74, 75, 76, 77, 78, 79, 80, 81}, 8: {66, 72, 75, 82, 83, 84, 85, 86, 87, 88, 89, 90, 91, 92}, 9: {96, 97, 98, 99, 100, 101, 102, 103, 93, 94, 95}, 10: {104, 105, 106, 107, 44, 108, 109, 110, 111, 112, 113, 51, 114, 55}, 11: {79, 115, 116, 117, 87}, 12: {96, 100, 43, 118, 119, 120, 121, 122, 123, 124, 125, 126}, 13: {128, 129, 130, 131, 132, 133, 134, 135, 136, 137, 74, 79, 80, 55, 87, 127}, 14: {138, 139, 140, 141, 142, 143, 144, 145, 146, 147, 148, 149, 150, 151, 152, 153}, 15: {160, 161, 162, 163, 164, 165, 166, 53, 154, 155, 156, 157, 158, 159}, 16: {98, 131, 167, 168, 169, 170, 171, 172, 173, 174, 175, 176, 177, 178, 179, 180, 181, 182, 183}, 17: {133, 137, 78, 79, 184, 185, 186, 187}, 18: {192, 193, 194, 36, 52, 18

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



['370', '58', '740']
{2: {32, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31}, 3: {33}, 4: {34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 24}, 5: {44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57}, 6: {64, 65, 66, 67, 68, 69, 70, 71, 58, 59, 60, 61, 62, 63}, 7: {72, 73, 74, 75, 76, 77, 78, 79, 80, 81}, 8: {66, 72, 75, 82, 83, 84, 85, 86, 87, 88, 89, 90, 91, 92}, 9: {96, 97, 98, 99, 100, 101, 102, 103, 93, 94, 95}, 10: {104, 105, 106, 107, 44, 108, 109, 110, 111, 112, 113, 51, 114, 55}, 11: {79, 115, 116, 117, 87}, 12: {96, 100, 43, 118, 119, 120, 121, 122, 123, 124, 125, 126}, 13: {128, 129, 130, 131, 132, 133, 134, 135, 136, 137, 74, 79, 80, 55, 87, 127}, 14: {138, 139, 140, 141, 142, 143, 144, 145, 146, 147, 148, 149, 150, 151, 152, 153}, 15: {160, 161, 162, 163, 164, 165, 166, 53, 154, 155, 156, 157, 158, 159}, 16: {98, 131, 167, 168, 169, 170, 171, 172, 173, 174, 175, 176, 177, 178, 179, 180, 181, 182, 183}, 17: {133, 137, 78, 79, 184, 185, 186, 187}, 18: {192, 193, 194, 36, 52, 18

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [26]:
len(item_set)

3846

In [50]:
# user_pos_ratings.items()

In [53]:
# item_index_old2new

In [54]:
# item_set

In [55]:
file_path3 = 'data/music/ratings_final.txt'

# Reading CSV and creating a DataFrame
df3 = pd.read_csv(file_path3, sep='\t', header=None, names=['user_index', 'item', 'target'])

# Display the DataFrame
print(df3)

       user_index  item  target
0               0    32       1
1               0    20       1
2               0    21       1
3               0    22       1
4               0    23       1
...           ...   ...     ...
42341        1871  3057       0
42342        1871  1630       0
42343        1871  1394       0
42344        1871  1410       0
42345        1871  2122       0

[42346 rows x 3 columns]


In [60]:
# Count the distinct values in each column
unique_values_user_index = df3['user_index'].nunique()
unique_values_item = df3['item'].nunique()

# Display the results
print("Distinct values count for 'user_index':", unique_values_user_index)
print("Distinct values count for 'item':", unique_values_item)

# Count unique pairs of two columns
unique_pairs_count = df3.groupby(['user_index', 'target']).size().reset_index(name='count')
# Display the result
print(unique_pairs_count.head(20))

Distinct values count for 'user_index': 1872
Distinct values count for 'item': 3846
    user_index  target  count
0            0       0     13
1            0       1     13
2            1       0      1
3            1       1      1
4            2       0     11
5            2       1     11
6            3       0     14
7            3       1     14
8            4       0     14
9            4       1     14
10           5       0     10
11           5       1     10
12           6       0     14
13           6       1     14
14           7       0     11
15           7       1     11
16           8       0     14
17           8       1     14
18           9       0      5
19           9       1      5


**convert_kg()** <br>
it creates a final kg_final.txt file with columns head, relation, tail by replacing the head and the tail of the kg.txt file with the updated satori_ids of the item_index2entity_id.txt file. If there are not such entities they are added with new indices <br>
The different types of relations are also put in a dictionary as keys with values integer numbers

In [61]:
entity_cnt = len(entity_id2index) #calculates the number of entities by getting the length of the entity_id2index dictionary
relation_cnt = 0

# writer = open('data/' + DATASET + '/kg_final.txt', 'w', encoding='utf-8') #opens a file named 'kg_final.txt' in the 'data/DATASET/' directory for writing
for line in open('data/' + 'music' + '/kg.txt', encoding='utf-8'): #opens another file named 'kg.txt' in the 'data/DATASET/' directory for reading
    array = line.strip().split('\t') #reads a line from the file, removes leading and trailing whitespace characters, and splits it into a list of strings using the tab character ('\t') as the delimiter. The resulting array should contain three elements: head, relation, and tail.
    head_old = array[0]
    relation_old = array[1]
    tail_old = array[2]

    # in lines 92-100 the head and tails that are not already in the satori ids, are added to the entity_id2index dictionary as keys and a new value is generated
    if head_old not in entity_id2index: #checks if head_old is not already in the entity_id2index dictionary, meaning it's a new entity.
        entity_id2index[head_old] = entity_cnt #If it's a new entity, it adds head_old to the entity_id2index dictionary and assigns it a new index (entity_cnt). This is likely used to create an index for the entity if it doesn't exist already.
        entity_cnt += 1
    head = entity_id2index[head_old] #retrieves the index associated with head_old from the entity_id2index dictionary and assigns it to the variable head.

    if tail_old not in entity_id2index: #checks if tail_old is not already in the entity_id2index dictionary, indicating a new entity.
        entity_id2index[tail_old] = entity_cnt #If it's a new entity, it adds tail_old to the entity_id2index dictionary and assigns it a new index (entity_cnt).
        entity_cnt += 1
    tail = entity_id2index[tail_old] #retrieves the index associated with tail_old from the entity_id2index dictionary and assigns it to the variable tail.

    if relation_old not in relation_id2index: # checks if relation_old is not already in the relation_id2index dictionary, indicating a new relation.
        relation_id2index[relation_old] = relation_cnt #If it's a new relation, it adds relation_old to the relation_id2index dictionary and assigns it a new index (relation_cnt). This is likely used to create an index for the relation if it doesn't exist already.
        relation_cnt += 1
    relation = relation_id2index[relation_old] #retrieves the index associated with relation_old from the relation_id2index dictionary and assigns it to the variable relation.

#     writer.write('%d\t%d\t%d\n' % (head, relation, tail)) #For each line in the 'kg.txt' file, this line writes a new line to the 'kg_final.txt' file with the format "head\trelation\ttail," where head, relation, and tail are the indices for the entities and relation.

# writer.close() #closes the 'kg_final.txt' file.
print('number of entities (containing items): %d' % entity_cnt)
print('number of relations: %d' % relation_cnt)

number of entities (containing items): 9366
number of relations: 60


In [63]:
relation_id2index

{'music.artist.origin': 0,
 'film.person_or_entity_appearing_in_film.film': 1,
 'film.actor.film': 2,
 'music.musician.instruments_played': 3,
 'people.person.place_of_birth': 4,
 'cvg.publisher.games_published': 5,
 'games.publisher.games_published': 6,
 'film.distributor.film': 7,
 'film.production_company.film': 8,
 'music.artist.album': 9,
 'film.writer.film': 10,
 'type.object.key': 11,
 'music.artist.track': 12,
 'award.winner.awards_won': 13,
 'film.film.language': 14,
 'award.competitor.awards_won': 15,
 'film.film.genre': 16,
 'music.producer.tracks_produced': 17,
 'film.director.film': 18,
 'event.agent.performance': 19,
 'film.film.star': 20,
 'film.film.writer': 21,
 'type.object.subject_key': 22,
 'people.deceased_person.place_of_death': 23,
 'people.person.profession': 24,
 'film.film.rating': 25,
 'music.album.genre': 26,
 'tv.program.genre': 27,
 'award.competitor.award_nominations': 28,
 'film.film.actor': 29,
 'award.nominee.award_nominations': 30,
 'music.album.track

In [64]:
file_path4 = 'data/music/kg.txt'

# Reading CSV and creating a DataFrame
df4 = pd.read_csv(file_path4, sep='\t', header=None, names=['head', 'relation', 'tail'])

# Display the DataFrame
print(df4)

       head                                      relation  tail
0      2086                           music.artist.origin  3846
1      1601  film.person_or_entity_appearing_in_film.film  3847
2      3355                               film.actor.film  3848
3      3798                           music.artist.origin  3849
4       427                           music.artist.origin  3850
...     ...                                           ...   ...
15513  3415                           music.artist.origin  5413
15514  3232                           music.artist.origin  4616
15515  2080                               film.actor.film  8058
15516  2080  film.person_or_entity_appearing_in_film.film  9361
15517  3102                           music.artist.origin  5213

[15518 rows x 3 columns]


In [68]:
# Count the distinct values in each column
unique_values_head = df4['head'].nunique()
unique_values_relation = df4['relation'].nunique()
unique_values_tail = df4['tail'].nunique()

# Display the results
print("Distinct values count for 'head':", unique_values_head)
print("Distinct values count for 'relation':", unique_values_relation)
print("Distinct values count for 'tail':", unique_values_tail)

# Get counts of values in 'your_column' and sort in descending order
value_counts_sorted = df4['relation'].value_counts().sort_values(ascending=False)

# Display the result
print("Counts of values in 'your_column' sorted in descending order:")
print(value_counts_sorted)

Distinct values count for 'head': 3846
Distinct values count for 'relation': 60
Distinct values count for 'tail': 5547
Counts of values in 'your_column' sorted in descending order:
film.actor.film                                 4623
film.person_or_entity_appearing_in_film.film    4582
music.artist.origin                             2536
people.person.place_of_birth                     946
film.distributor.film                            500
film.production_company.film                     439
music.artist.album                               212
music.musician.instruments_played                199
cvg.publisher.games_published                    175
games.publisher.games_published                  175
people.deceased_person.place_of_death            148
event.agent.performance                           97
award.competitor.award_nominations                72
award.nominee.award_nominations                   72
music.artist.track                                66
film.director.film      

In [69]:
file_path5 = 'data/music/kg_final.txt'

# Reading CSV and creating a DataFrame
df5 = pd.read_csv(file_path5, sep='\t', header=None, names=['head', 'relation', 'tail'])

# Display the DataFrame
print(df5)

       head  relation  tail
0      2086         0  3846
1      1601         1  3847
2      3355         2  3848
3      3798         0  3849
4       427         0  3850
...     ...       ...   ...
15513  3415         0  5413
15514  3232         0  4616
15515  2080         2  8058
15516  2080         1  9361
15517  3102         0  5213

[15518 rows x 3 columns]


In [70]:
# Count the distinct values in each column
unique_values_head_f = df5['head'].nunique()
unique_values_relation_f = df5['relation'].nunique()
unique_values_tail_f = df5['tail'].nunique()

# Display the results
print("Distinct values count for 'head':", unique_values_head_f)
print("Distinct values count for 'relation':", unique_values_relation_f)
print("Distinct values count for 'tail':", unique_values_tail_f)

# Get counts of values in 'your_column' and sort in descending order
value_counts_sorted_f = df5['relation'].value_counts().sort_values(ascending=False)

# Display the result
print("Counts of values in 'your_column' sorted in descending order:")
print(value_counts_sorted_f)

Distinct values count for 'head': 3846
Distinct values count for 'relation': 60
Distinct values count for 'tail': 5547
Counts of values in 'your_column' sorted in descending order:
2     4623
1     4582
0     2536
4      946
7      500
8      439
9      212
3      199
6      175
5      175
23     148
19      97
28      72
30      72
12      66
18      63
10      63
17      59
24      55
26      48
16      38
33      34
13      27
15      27
22      26
14      25
29      24
11      23
20      17
21      16
38      15
34      13
43      11
27      11
46       8
36       7
50       6
25       6
37       6
51       5
58       5
31       5
32       5
39       4
41       3
35       3
44       2
48       2
40       2
42       2
53       1
54       1
59       1
56       1
47       1
45       1
52       1
57       1
49       1
55       1
Name: relation, dtype: int64


# data_loader.py

load_rating()

In [73]:
rating_file = 'data/' + 'music' + '/ratings_final' # '../data/' + args.dataset + '/ratings_final'
if os.path.exists(rating_file + '.npy'):
    rating_np = np.load(rating_file + '.npy')
else:
    rating_np = np.loadtxt(rating_file + '.txt', dtype=np.int64)
    np.save(rating_file + '.npy', rating_np)

n_user = len(set(rating_np[:, 0]))
n_item = len(set(rating_np[:, 1]))

In [74]:
rating_np

array([[   0,   32,    1],
       [   0,   20,    1],
       [   0,   21,    1],
       ...,
       [1871, 1394,    0],
       [1871, 1410,    0],
       [1871, 2122,    0]], dtype=int64)

In [75]:
print(n_user)
print(n_item)

1872
3846


dataset_split()

In [76]:
rating_np.shape

(42346, 3)

In [80]:
n_ratings = rating_np.shape[0]
list(range(n_ratings))

[0,
 1,
 2,
 3,
 4,
 5,
 6,
 7,
 8,
 9,
 10,
 11,
 12,
 13,
 14,
 15,
 16,
 17,
 18,
 19,
 20,
 21,
 22,
 23,
 24,
 25,
 26,
 27,
 28,
 29,
 30,
 31,
 32,
 33,
 34,
 35,
 36,
 37,
 38,
 39,
 40,
 41,
 42,
 43,
 44,
 45,
 46,
 47,
 48,
 49,
 50,
 51,
 52,
 53,
 54,
 55,
 56,
 57,
 58,
 59,
 60,
 61,
 62,
 63,
 64,
 65,
 66,
 67,
 68,
 69,
 70,
 71,
 72,
 73,
 74,
 75,
 76,
 77,
 78,
 79,
 80,
 81,
 82,
 83,
 84,
 85,
 86,
 87,
 88,
 89,
 90,
 91,
 92,
 93,
 94,
 95,
 96,
 97,
 98,
 99,
 100,
 101,
 102,
 103,
 104,
 105,
 106,
 107,
 108,
 109,
 110,
 111,
 112,
 113,
 114,
 115,
 116,
 117,
 118,
 119,
 120,
 121,
 122,
 123,
 124,
 125,
 126,
 127,
 128,
 129,
 130,
 131,
 132,
 133,
 134,
 135,
 136,
 137,
 138,
 139,
 140,
 141,
 142,
 143,
 144,
 145,
 146,
 147,
 148,
 149,
 150,
 151,
 152,
 153,
 154,
 155,
 156,
 157,
 158,
 159,
 160,
 161,
 162,
 163,
 164,
 165,
 166,
 167,
 168,
 169,
 170,
 171,
 172,
 173,
 174,
 175,
 176,
 177,
 178,
 179,
 180,
 181,
 182,
 183,
 184,


load_kg()

In [81]:
kg_file = 'data/' + 'music' + '/kg_final'
if os.path.exists(kg_file + '.npy'):
    kg_np = np.load(kg_file + '.npy')
else:
    kg_np = np.loadtxt(kg_file + '.txt', dtype=np.int64)
    np.save(kg_file + '.npy', kg_np)

n_entity = len(set(kg_np[:, 0]) | set(kg_np[:, 2]))
n_relation = len(set(kg_np[:, 1]))

In [82]:
print(len(set(kg_np[:, 0])))
print(len(set(kg_np[:, 2])))
print(n_entity)
print(n_relation)

3846
5547
9366
60


In [83]:
kg_np

array([[2086,    0, 3846],
       [1601,    1, 3847],
       [3355,    2, 3848],
       ...,
       [2080,    2, 8058],
       [2080,    1, 9361],
       [3102,    0, 5213]], dtype=int64)

construct_kg()

In [84]:
kg = dict()
# Iterate over each triple in the KG
for triple in kg_np:
    head = triple[0]
    relation = triple[1]
    tail = triple[2]
    # treat the KG as an undirected graph
    if head not in kg:
        kg[head] = []
    kg[head].append((tail, relation))
    if tail not in kg:
        kg[tail] = []
    kg[tail].append((head, relation))

In [85]:
kg

{2086: [(3846, 0)],
 3846: [(2086, 0),
  (2232, 0),
  (3454, 0),
  (1772, 0),
  (3382, 23),
  (359, 4),
  (896, 4),
  (3133, 0),
  (3791, 4),
  (3343, 0),
  (1599, 4),
  (1278, 4),
  (1079, 4),
  (2582, 4),
  (1371, 0),
  (1970, 0),
  (753, 0),
  (1767, 4),
  (1770, 4),
  (2673, 23),
  (2824, 0),
  (1958, 0),
  (1226, 0),
  (3460, 0),
  (1771, 0),
  (632, 23),
  (1517, 23),
  (1767, 23),
  (2766, 23),
  (3800, 0),
  (59, 23),
  (513, 0),
  (2610, 4),
  (80, 4),
  (2777, 0),
  (3221, 4),
  (1728, 0),
  (2947, 4),
  (1482, 0)],
 1601: [(3847, 1),
  (4021, 2),
  (4022, 1),
  (4674, 2),
  (5629, 2),
  (6066, 2),
  (3847, 2),
  (4021, 1),
  (6952, 2),
  (4674, 1),
  (7191, 2),
  (7222, 1),
  (7372, 2),
  (6952, 1),
  (7892, 2),
  (7914, 1),
  (8059, 1),
  (7372, 1),
  (8415, 1),
  (5629, 1),
  (4022, 2),
  (8415, 2),
  (8612, 1),
  (8839, 2),
  (7191, 1),
  (8955, 1),
  (8977, 1),
  (6066, 1),
  (9037, 1),
  (7892, 1),
  (7222, 2),
  (7914, 2),
  (8612, 2),
  (8839, 1),
  (9037, 2),
  (8059

In [86]:
number_of_kg_entities = len(kg)
number_of_kg_entities

9366

construct_adj()

In [103]:
entity_num=n_entity
adj_entity = np.zeros([entity_num, 8], dtype=np.int64)
adj_relation = np.zeros([entity_num, 8], dtype=np.int64)
for entity in range(entity_num):
    neighbors = kg[entity]
    n_neighbors = len(neighbors)
#     print(entity)
#     print(neighbors)
#     print(n_neighbors)
    if n_neighbors >= 8:
        sampled_indices = np.random.choice(list(range(n_neighbors)), size=8, replace=False)
#         print(entity)
#         print(neighbors)
#         print(n_neighbors)
#         print(sampled_indices)
    else:
        sampled_indices = np.random.choice(list(range(n_neighbors)), size=8, replace=True)
#         print(entity)
#         print(neighbors)
#         print(n_neighbors)
#         print(sampled_indices)
    adj_entity[entity] = np.array([neighbors[i][0] for i in sampled_indices])
    adj_relation[entity] = np.array([neighbors[i][1] for i in sampled_indices])


In [104]:
adj_entity

array([[4454, 4454, 4454, ..., 4454, 4454, 4454],
       [7498, 7498, 7498, ..., 7498, 7498, 7498],
       [5845, 5845, 5845, ..., 5845, 5845, 5845],
       ...,
       [1204, 1204, 1204, ..., 1204, 1204, 1204],
       [2293, 2293, 2293, ..., 2293, 2293, 2293],
       [2241, 2241, 2241, ..., 2241, 2241, 2241]], dtype=int64)

In [105]:
adj_relation

array([[0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       ...,
       [1, 2, 2, ..., 1, 2, 1],
       [1, 1, 2, ..., 2, 2, 2],
       [8, 8, 8, ..., 7, 8, 7]], dtype=int64)

In [100]:
adj_relation.shape

(9366, 8)

# Run preprocess.py and data_loader.py to create the datasets used in the train.py

In [1]:
import argparse
import numpy as np
from time import time

class CustomArgs:
    def __init__(self):
        self.batch_size = 128
        self.dataset = 'music'
        self.dim = 16
        self.l2_weight = 1e-4
        self.lr = 5e-4
        self.ls_weight = 0.1
        self.n_epochs = 10
        self.n_iter = 1
        self.neighbor_sample_size = 8
        
args = CustomArgs()
# print(args.batch_size)
# print(args.l2_weight)

In [2]:
############################### preprocess.py

# DATASET = 'music'
# entity_id2index = dict() #initialize three dictionaries: entity_id2index, relation_id2index, and item_index_old2new. These dictionaries are likely intended to store mappings between IDs and indices for entities, relations, and items.
# relation_id2index = dict()
# item_index_old2new = dict()

RATING_FILE_NAME = dict({'movie': 'ratings.csv', 'book': 'BX-Book-Ratings.csv', 'music': 'user_artists.dat'})
SEP = dict({'movie': ',', 'book': ';', 'music': '\t'})
THRESHOLD = dict({'movie': 4, 'book': 0, 'music': 0})

# This function reads and processes a file that maps item indexes to entity IDs, and it creates mappings between these IDs and their corresponding indices, stored in the item_index_old2new and entity_id2index dictionaries.
def read_item_index_to_entity_id_file():
    file = 'data/' + DATASET + '/item_index2entity_id.txt' #'../data/' + DATASET + '/item_index2entity_id.txt' Constructs the path of the item index to entity ID mapping file
    print('reading item index to entity id file: ' + file + ' ...')
    i = 0 #This variable is likely to be used for indexing
    for line in open(file, encoding='utf-8').readlines(): # reads the file's content line by line
        item_index = line.strip().split('\t')[0] # removes leading and trailing whitespace characters, splits the line into a list of strings and selects the first element which is assumed to be the item index
        satori_id = line.strip().split('\t')[1] # extracts the second element from the list, which is assumed to be the Satori ID
        item_index_old2new[item_index] = i #This line updates a dictionary named item_index_old2new. It uses the item_index as the key and assigns the value i to it. This is likely used to map old item indexes to new ones.
        entity_id2index[satori_id] = i #This line updates a dictionary named entity_id2index. It uses the satori_id as the key and assigns the value i to it. This is likely used to map entity IDs to their corresponding indices.
        i += 1


def convert_rating():
    file = 'data/' + DATASET + '/' + RATING_FILE_NAME[DATASET] #'../data/' + DATASET + '/' + RATING_FILE_NAME[DATASET] Constructs a file path by combining the string 'data/' with the value of the variable DATASET and the filename specified in the RATING_FILE_NAME dictionary for the given dataset.

    print('reading rating file ...')
    item_set = set(item_index_old2new.values()) # creates a set called item_set that contains unique values from the item_index_old2new dictionary (the values not the keys). It collects all unique item indices.
    user_pos_ratings = dict() #These two lines create two dictionaries, user_pos_ratings and user_neg_ratings, to store positive and negative user ratings. These dictionaries will map user IDs to sets of items.
    user_neg_ratings = dict()

    for line in open(file, encoding='utf-8').readlines()[1:]: #It then iterates through the lines in the file, skipping the first line which is the header)
        array = line.strip().split(SEP[DATASET]) #reads a line from the file, removes leading and trailing whitespace characters, and splits it into a list of strings using the delimiter specified in the SEP dictionary for the given dataset.

        # remove prefix and suffix quotation marks for BX dataset
        if DATASET == 'book':
            array = list(map(lambda x: x[1:-1], array)) # the map() function executes a specified function for each item in an iterable

        # in lines 37-44, it keeps only the lines where the artist ids exist in the item indices of the item_index2entity_id.tx file and for each artistID it keeps the new item_index created with the read_item_index_to_entity_id_file function
        item_index_old = array[1] #extracts the item index from the array.
        if item_index_old not in item_index_old2new:  # the item is not in the final item set
            continue # if the item index is not in the item_index_old2new dictionary, it skips to the next iteration of the loop. This is likely used to filter out items that are not in the final item set
        item_index = item_index_old2new[item_index_old] #maps the old item index to a new item index using the item_index_old2new dictionary.

        user_index_old = int(array[0]) # extracts the user index (converting it to an integer) from the array.

        rating = float(array[2]) #  extracts the rating (as a floating-point number) from the array.

        # in lines 47-54 creates a positive and a negative dictionary where the keys are the userIDs and their corresponding value is a list with all the new item indices of the artistIDs i.e. {2: {32, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31}, 3: {33}, 4: {24, 34, 35}}
        if rating >= THRESHOLD[DATASET]: # checks if the rating is greater than or equal to a threshold value specified in the THRESHOLD dictionary for the given dataset.
            if user_index_old not in user_pos_ratings: # it adds the user_index_old to the user_pos_ratings dictionary, creating a set for the user if it doesn't exist, and adds the item_index to the set.
                user_pos_ratings[user_index_old] = set()
            user_pos_ratings[user_index_old].add(item_index)
        else:
            if user_index_old not in user_neg_ratings:
                user_neg_ratings[user_index_old] = set()
            user_neg_ratings[user_index_old].add(item_index)

    print('converting rating file ...')
    writer = open('data/' + DATASET + '/ratings_final.txt', 'w', encoding='utf-8') #../ opens a new file for writing, named 'ratings_final.txt'
    user_cnt = 0
    user_index_old2new = dict()
    # in lines 61-65 creates new indices fot the userIDs in the positive ratings dictionary
    for user_index_old, pos_item_set in user_pos_ratings.items(): # iterates through the users in the user_pos_ratings dictionary and their associated positive item sets.
        if user_index_old not in user_index_old2new: # checks if the old user index is not already in the user_index_old2new dictionary.
            user_index_old2new[user_index_old] = user_cnt # If the user index is not in the dictionary, it adds the user index to the user_index_old2new dictionary and assigns a new index (user_cnt) to it.
            user_cnt += 1 #  increments user_cnt to ensure that the new user indices are unique.
        user_index = user_index_old2new[user_index_old] #obtains the new user index from the user_index_old2new dictionary.

        for item in pos_item_set: # iterates through the positive item set associated with the user.
            writer.write('%d\t%d\t1\n' % (user_index, item)) #For each user-item pair, it writes a line to the 'ratings_final.txt' file in the format "user_index\titem\t1". This is likely to represent a positive rating (1).
        unwatched_set = item_set - pos_item_set # calculates a set of unwatched items by taking the difference between the item_set (all items) and the pos_item_set (items the user has positively rated).
        if user_index_old in user_neg_ratings: #checks if the user has negative ratings in the user_neg_ratings dictionary.
            unwatched_set -= user_neg_ratings[user_index_old] #If there are negative ratings, it removes items in the user_neg_ratings set from the unwatched_set.
        for item in np.random.choice(list(unwatched_set), size=len(pos_item_set), replace=False): # it randomly selects items from the unwatched_set using NumPy's random.choice function. The number of items selected is equal to the length of the pos_item_set, and items are not replaced after selection (replace=False).
            writer.write('%d\t%d\t0\n' % (user_index, item)) #For each user-item pair, it writes a line to the 'ratings_final.txt' file in the format "user_index\titem\t0". This is likely to represent a negative rating (0).
    writer.close() #closes the 'ratings_final.txt' file.
    print('number of users: %d' % user_cnt)
    print('number of items: %d' % len(item_set)) #number of unique items


def convert_kg():
    print('converting kg file ...')
    entity_cnt = len(entity_id2index) #calculates the number of entities by getting the length of the entity_id2index dictionary
    relation_cnt = 0

    writer = open('data/' + DATASET + '/kg_final.txt', 'w', encoding='utf-8') #opens a file named 'kg_final.txt' in the 'data/DATASET/' directory for writing
    for line in open('data/' + DATASET + '/kg.txt', encoding='utf-8'): #opens another file named 'kg.txt' in the 'data/DATASET/' directory for reading
        array = line.strip().split('\t') #reads a line from the file, removes leading and trailing whitespace characters, and splits it into a list of strings using the tab character ('\t') as the delimiter. The resulting array should contain three elements: head, relation, and tail.
        head_old = array[0]
        relation_old = array[1]
        tail_old = array[2]

        # in lines 92-100 the head and tails that are not already in the satori ids, are added to the entity_id2index dictionary as keys and a new value is generated
        if head_old not in entity_id2index: #checks if head_old is not already in the entity_id2index dictionary, meaning it's a new entity.
            entity_id2index[head_old] = entity_cnt #If it's a new entity, it adds head_old to the entity_id2index dictionary and assigns it a new index (entity_cnt). This is likely used to create an index for the entity if it doesn't exist already.
            entity_cnt += 1
        head = entity_id2index[head_old] #retrieves the index associated with head_old from the entity_id2index dictionary and assigns it to the variable head.

        if tail_old not in entity_id2index: #checks if tail_old is not already in the entity_id2index dictionary, indicating a new entity.
            entity_id2index[tail_old] = entity_cnt #If it's a new entity, it adds tail_old to the entity_id2index dictionary and assigns it a new index (entity_cnt).
            entity_cnt += 1
        tail = entity_id2index[tail_old] #retrieves the index associated with tail_old from the entity_id2index dictionary and assigns it to the variable tail.

        if relation_old not in relation_id2index: # checks if relation_old is not already in the relation_id2index dictionary, indicating a new relation.
            relation_id2index[relation_old] = relation_cnt #If it's a new relation, it adds relation_old to the relation_id2index dictionary and assigns it a new index (relation_cnt). This is likely used to create an index for the relation if it doesn't exist already.
            relation_cnt += 1
        relation = relation_id2index[relation_old] #retrieves the index associated with relation_old from the relation_id2index dictionary and assigns it to the variable relation.

        writer.write('%d\t%d\t%d\n' % (head, relation, tail)) #For each line in the 'kg.txt' file, this line writes a new line to the 'kg_final.txt' file with the format "head\trelation\ttail," where head, relation, and tail are the indices for the entities and relation.

    writer.close() #closes the 'kg_final.txt' file.
    print('number of entities (containing items): %d' % entity_cnt)
    print('number of relations: %d' % relation_cnt)



############ data_loader.py

import numpy as np
import os


def load_data(args):
    n_user, n_item, train_data, eval_data, test_data = load_rating(args)
    n_entity, n_relation, adj_entity, adj_relation = load_kg(args)
    print('data loaded.')

    return n_user, n_item, n_entity, n_relation, train_data, eval_data, test_data, adj_entity, adj_relation


def load_rating(args):
    print('reading rating file ...')

    # reading rating file
    rating_file = 'data/' + args.dataset + '/ratings_final' # '../data/' + args.dataset + '/ratings_final'
    # Check if a preprocessed numpy file exists, if not, load the text file and save it as a numpy file
    if os.path.exists(rating_file + '.npy'):
        rating_np = np.load(rating_file + '.npy')
    else:
        rating_np = np.loadtxt(rating_file + '.txt', dtype=np.int64)
        np.save(rating_file + '.npy', rating_np)

    # Compute the number of users and items
    n_user = len(set(rating_np[:, 0]))
    n_item = len(set(rating_np[:, 1]))
    train_data, eval_data, test_data = dataset_split(rating_np, args) # Split the dataset into training, evaluation, and testing sets

    return n_user, n_item, train_data, eval_data, test_data


def dataset_split(rating_np, args):
    print('splitting dataset ...')

    # train:eval:test = 6:2:2
    eval_ratio = 0.2
    test_ratio = 0.2
    n_ratings = rating_np.shape[0] # number of total ratings

    eval_indices = np.random.choice(list(range(n_ratings)), size=int(n_ratings * eval_ratio), replace=False) # randomly select indices for the evaluation set
    left = set(range(n_ratings)) - set(eval_indices) # indices left after removing the ones that were chosen for evaluation
    test_indices = np.random.choice(list(left), size=int(n_ratings * test_ratio), replace=False) # randomly select from the left indices for the test set
    train_indices = list(left - set(test_indices)) # from the left indices remove the test indices to create the train ones

    train_data = rating_np[train_indices]
    eval_data = rating_np[eval_indices]
    test_data = rating_np[test_indices]

    return train_data, eval_data, test_data


def load_kg(args):
    print('reading KG file ...')

    # reading kg file
    kg_file = 'data/' + args.dataset + '/kg_final'
    if os.path.exists(kg_file + '.npy'):
        kg_np = np.load(kg_file + '.npy')
    else:
        kg_np = np.loadtxt(kg_file + '.txt', dtype=np.int64)
        np.save(kg_file + '.npy', kg_np)

    n_entity = len(set(kg_np[:, 0]) | set(kg_np[:, 2])) # number of total distinct entities in heads and tails
    n_relation = len(set(kg_np[:, 1])) # number of relations

    kg = construct_kg(kg_np)
    adj_entity, adj_relation = construct_adj(args, kg, n_entity)

    return n_entity, n_relation, adj_entity, adj_relation


# Define a function to construct the KG as a dictionary of entities and their relations
def construct_kg(kg_np):
    print('constructing knowledge graph ...')
    kg = dict()
    # Iterate over each triple in the KG
    for triple in kg_np:
        head = triple[0]
        relation = triple[1]
        tail = triple[2]
        # treat the KG as an undirected graph
        if head not in kg:
            kg[head] = []
        kg[head].append((tail, relation))
        if tail not in kg:
            kg[tail] = []
        kg[tail].append((head, relation))
    return kg

# Define a function to construct adjacency matrices for entities and relations
def construct_adj(args, kg, entity_num):
    print('constructing adjacency matrix ...')
    # each line of adj_entity stores the sampled neighbor entities for a given entity
    # each line of adj_relation stores the corresponding sampled neighbor relations
    adj_entity = np.zeros([entity_num, args.neighbor_sample_size], dtype=np.int64)
    adj_relation = np.zeros([entity_num, args.neighbor_sample_size], dtype=np.int64)
    for entity in range(entity_num):
        neighbors = kg[entity]
        n_neighbors = len(neighbors)
        if n_neighbors >= args.neighbor_sample_size: # if neighbors more than threshold, then sample indices of neighbors
            sampled_indices = np.random.choice(list(range(n_neighbors)), size=args.neighbor_sample_size, replace=False)
        else: # if neighbors less than threshold, then sample indices of neighbors with replacement in order to have vectors of equal size
            sampled_indices = np.random.choice(list(range(n_neighbors)), size=args.neighbor_sample_size, replace=True)
        adj_entity[entity] = np.array([neighbors[i][0] for i in sampled_indices]) # replace the 0 value with the entity id
        adj_relation[entity] = np.array([neighbors[i][1] for i in sampled_indices]) # replace the 0 value with the relation id

    return adj_entity, adj_relation





data = load_data(args)

reading rating file ...
splitting dataset ...
reading KG file ...
constructing knowledge graph ...
constructing adjacency matrix ...
data loaded.


In [5]:
n_user, n_item, n_entity, n_relation = data[0], data[1], data[2], data[3]
train_data, eval_data, test_data = data[4], data[5], data[6]
adj_entity, adj_relation = data[7], data[8]

# train.py

In [6]:
print(n_user)
print(n_item)
print(n_entity)
print(n_relation)

1872
3846
9366
60


In [7]:
print(train_data)
print(eval_data)
print(test_data)

[[   0   21    1]
 [   0   23    1]
 [   0   27    1]
 ...
 [1871 1394    0]
 [1871 1410    0]
 [1871 2122    0]]
[[ 856  126    1]
 [ 563  257    1]
 [ 343 2374    0]
 ...
 [ 381  570    0]
 [1279 1658    0]
 [ 109  783    1]]
[[ 867 1586    0]
 [ 524 1807    1]
 [ 428  557    1]
 ...
 [ 281 3440    0]
 [1100  192    1]
 [1870 3839    1]]


In [8]:
print(adj_entity)
print(adj_relation)

[[4454 4454 4454 ... 4454 4454 4454]
 [7498 7498 7498 ... 7498 7498 7498]
 [5845 5845 5845 ... 5845 5845 5845]
 ...
 [1204 1204 1204 ... 1204 1204 1204]
 [2293 2293 2293 ... 2293 2293 2293]
 [2241 2241 2241 ... 2241 2241 2241]]
[[0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 ...
 [1 1 1 ... 2 2 2]
 [1 1 2 ... 2 2 2]
 [7 8 7 ... 7 8 8]]


get_interaction_table()

In [3]:
import tensorflow as tf

In [9]:
offset = len(str(n_entity))
offset = 10 ** offset
keys = train_data[:, 0] * offset + train_data[:, 1]
keys = keys.astype(np.int64)
values = train_data[:, 2].astype(np.float32)

interaction_table = tf.contrib.lookup.HashTable(
    tf.contrib.lookup.KeyValueTensorInitializer(keys=keys, values=values), default_value=0.5)

The TensorFlow contrib module will not be included in TensorFlow 2.0.
For more information, please see:
  * https://github.com/tensorflow/community/blob/master/rfcs/20180907-contrib-sunset.md
  * https://github.com/tensorflow/addons
  * https://github.com/tensorflow/io (for I/O related ops)
If you depend on functionality not listed there, please file an issue.



In [12]:
print(offset)
print(train_data[:, 0])
print(train_data[:, 1])
print(keys)
print(values)


10000
[   0    0    0 ... 1871 1871 1871]
[  21   23   27 ... 1394 1410 2122]
[      21       23       27 ... 18711394 18711410 18712122]
[1. 1. 1. ... 0. 0. 0.]


In [11]:
interaction_table

In [13]:
Initializer=tf.contrib.lookup.KeyValueTensorInitializer(keys=keys, values=values)

In [14]:
Initializer